<a href="https://colab.research.google.com/github/claudelepere/ML_GitHub/blob/main/Prediction_EN_791112_50000_51000_epoch5_shuffled_and_rare_labels_removed_041218.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

### Error: gcsfs 2024.10.0 requires fsspec==2024.10.0, but you have fsspec 2024.9.0 which is incompatible.
Ignore this error as gcsfs is not used.

## TO DO BEFORE RUN
- GIVE HF HUB AND W&B ACCESSES
- ADAPT HF HUB MODEL ID

In [ ]:
!pip install -q accelerate
!pip install -q huggingface_hub
#!pip install -q scikit-learn
!pip install -q transformers datasets  # 2 Hugging Face libraries
#!pip install -q wandb

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 2.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 103.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 82.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 54.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 1.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 11.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 41.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 9.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 11.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 97.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 491.2/491.2 kB 36.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 12.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

In [ ]:
import datetime
import json
import matplotlib.pyplot as plt
import numpy as np
import os
import pandas as pd
import shutil
import torch

from contextlib       import suppress
from datasets         import DatasetDict
from google.colab     import files, userdata
from huggingface_hub  import create_repo, hf_hub_download, login, whoami
from sklearn.metrics  import classification_report
from transformers     import LongformerTokenizerFast, LongformerForSequenceClassification
from torch.utils.data import DataLoader

## Hugging Face Hub (HF Hub) authenticate

In [ ]:
os.environ["HF_TOKEN"] = userdata.get("HF_TOKEN")    # Store the key in os.environ
hf_token               = os.environ.get('HF_TOKEN')

login(token=hf_token)

# Check
user = whoami(token=hf_token)
assert user['name'] == 'claudelepere', f"{user['name']} is not claudelepere"

print(f"user: {user}")

Note: Environment variable`HF_TOKEN` is set and is the current active token independently from the token you've just configured.


user: {'type': 'user', 'id': '66ec3d5f61228b02f8780beb', 'name': 'claudelepere', 'fullname': 'Claude Lepère', 'isPro': False, 'avatarUrl': 'https://cdn-avatars.huggingface.co/v1/production/uploads/66ec3d5f61228b02f8780beb/gvnf9pvm2KvE90ETMUQo3.jpeg', 'orgs': [], 'auth': {'type': 'access_token', 'accessToken': {'displayName': 'jobs_token', 'role': 'fineGrained', 'createdAt': '2025-01-04T17:44:35.493Z', 'fineGrained': {'canReadGatedRepos': False, 'global': [], 'scoped': [{'entity': {'_id': '66ec3d5f61228b02f8780beb', 'type': 'user', 'name': 'claudelepere'}, 'permissions': ['repo.content.read', 'repo.write']}]}}}}


## HF Hub repo

In [ ]:
repo_id = "claudelepere/jobs_EN_791112_50000_041218"

## Checks

In [ ]:
!python -V

print(f"currentdir: {os.getcwd()}")

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"device: {device}")

Python 3.11.12
currentdir: /content
device: cuda


In [ ]:
skills           = 791112
all_rows_low     = 50000
all_rows_high    = 51000
num_datapoints   = all_rows_high - all_rows_low
max_length       = 1024
batch_size       = 4*8
threshold_tuning = True

datasetDict_zip_file_name = f"dataset_EN_{skills}_{all_rows_low}_{all_rows_high}.zip"
datasetDict_dir_name      = os.path.splitext(datasetDict_zip_file_name)[0]

print(f"datasetDict_zip_file_name: {datasetDict_zip_file_name}")
print(f"datasetDict_dir_name     : {datasetDict_dir_name}")
print()


datasetDict_zip_file_name: dataset_EN_791112_50000_51000.zip
datasetDict_dir_name     : dataset_EN_791112_50000_51000



## Out Of Memory (OOM)

### OOM: check for and kill zombie processes

In [ ]:
!ps aux | grep python
!kill -9 <PID>
if torch.cuda.is_available():
    !nvidia-smi
    print(torch.cuda.memory_summary())

root          87  5.2  0.0      0     0 ?        Z    16:06   0:13 [python3] <defunct>
root          88  0.1  0.0  76328 57756 ?        S    16:06   0:00 python3 /usr/local/bin/colab-fileshim.py
root         133  1.4  0.1 793112 129804 ?       Sl   16:06   0:03 /usr/bin/python3 /usr/local/bin/jupyter-notebook --debug --transport="ipc" --ip=172.28.0.12 --NotebookApp.token= --port=9000 --FileContentsManager.root_dir=/ --MappingKernelManager.root_dir=/content
root         728 14.4  1.4 12270592 1274372 ?    Ssl  16:08   0:16 /usr/bin/python3 -m colab_kernel_launcher -f /root/.local/share/jupyter/runtime/kernel-7d62728d-5e91-471d-82c9-d9876db689de.json
root         768  0.5  0.0 544676 20224 ?        Sl   16:08   0:00 /usr/bin/python3 /usr/local/lib/python3.11/dist-packages/debugpy/adapter --for-server 41003 --host 127.0.0.1 --port 33269 --server-access-token 3119ed35efcfd330d05ed454a405e74524691abbc16a0bf180c318ec5f5e9661
root        1383  2.0  0.0 1241984 18340 ?       Sl   16:10   0:00 

### OOM: free up GPU memory

In [ ]:
torch.cuda.empty_cache()

## Upload and unzip job dataset

In [ ]:
def upload_unzip_dataset(filename):
    """Upload and unzip the dataset to /content, ensuring correct placement."""

    # Get the expected directory name (same as the zip filename without extension)
    expected_dir = os.path.splitext(filename)[0]

    # Check if the file and the directory exist in /content and delete them
    with suppress(FileNotFoundError):
        if os.path.isdir(expected_dir):
            shutil.rmtree(expected_dir)               # Remove directory if it exists
        if os.path.isfile(filename):
            os.remove(filename)                       # Remove file if it exists

    print(f"Removed '{expected_dir}' and '{filename}' if they were present in /content.")

    # Upload the zip file
    uploaded_files = files.upload()                  # Prompt file upload dialog

    if filename not in uploaded_files:
        raise FileNotFoundError(f"'{filename}' was not uploaded.")

    print(f"'{filename}' successfully uploaded to /content.")

    # Unzip the file to /content
    shutil.unpack_archive(filename, "/content")

    print(f"Unzipped to '/content/{expected_dir}'.")

# Usage
upload_unzip_dataset(datasetDict_zip_file_name)

Removed 'dataset_EN_791112_50000_51000' and 'dataset_EN_791112_50000_51000.zip' if they were present in /content.


Saving dataset_EN_791112_50000_51000.zip to dataset_EN_791112_50000_51000.zip
'dataset_EN_791112_50000_51000.zip' successfully uploaded to /content.
Unzipped to '/content/dataset_EN_791112_50000_51000'.


## Create datasetDict (HF DatasetDict) = 1 HF Dataset prediction
The sequence of datapoints of dataset=datasetDict['prediction'] is the same as the sequence of SELECT, id, ... WHERE in_LanguageId=1 ORDER BY id DESC in MySQL.

In [ ]:
datasetDict = DatasetDict.load_from_disk(datasetDict_dir_name)
dataset     = datasetDict['prediction']

print(f"dataset: {type(dataset)} shape={dataset.shape}\n{dataset}")     # <class 'datasets.arrow_dataset.Dataset'> shape=(100, 8)
print(f"dataset.features: {type(dataset.features)} shape={dataset.features}\n{dataset.features}")

# Convert the dataset to a pandas dataframe
df_original = pd.DataFrame(dataset)
print(f"df_original: {type(df_original)} shape={df_original.shape}\n{df_original}")                         # <class 'pandas.core.frame.DataFrame'> shape=(100, 8)


dataset: <class 'datasets.arrow_dataset.Dataset'> shape=(1000, 128)
Dataset({
    features: ['id', 'text', '142', '143', '146', '147', '149', '150', '152', '154', '155', '156', '158', '160', '162', '165', '167', '169', '170', '171', '173', '174', '175', '176', '356', '360', '361', '362', '364', '370', '371', '373', '375', '376', '394', '408', '667', '686', '687', '689', '756', '758', '760', '761', '906', '263', '265', '266', '267', '268', '271', '272', '273', '274', '275', '276', '277', '278', '279', '283', '284', '285', '286', '287', '288', '289', '291', '293', '297', '298', '299', '300', '301', '302', '303', '304', '358', '359', '365', '367', '379', '382', '385', '409', '610', '611', '613', '614', '615', '618', '637', '668', '670', '676', '677', '681', '682', '683', '811', '812', '813', '814', '815', '816', '817', '818', '819', '820', '821', '822', '823', '824', '825', '826', '827', '828', '829', '830', '135', '390', '136', '137', '138', '139', '350', '351', '352', '353'],
    num_ro

## Create labels (list), id2label (dict) and label2id (dict).
**The sequence of the labels list is the same as in dataset.
And the sequences of the optimized thresholds, true labels and predictions are preserved.**

* dataset 7_1000_125_125  ,  48 labels
* dataset 7_128_18_54     ,  42 labels
* dataset 8910_1087_68_204, 206 labels
* dataset 11_1000         ,   6 labels

In [ ]:
labels = [label for label in dataset.features.keys() if label not in ['id', 'text']]
#labels.sort()

print(f"labels: {type(labels)} {len(labels)}\n{labels}")

num_labels = len(labels)

labels: <class 'list'> 126
['142', '143', '146', '147', '149', '150', '152', '154', '155', '156', '158', '160', '162', '165', '167', '169', '170', '171', '173', '174', '175', '176', '356', '360', '361', '362', '364', '370', '371', '373', '375', '376', '394', '408', '667', '686', '687', '689', '756', '758', '760', '761', '906', '263', '265', '266', '267', '268', '271', '272', '273', '274', '275', '276', '277', '278', '279', '283', '284', '285', '286', '287', '288', '289', '291', '293', '297', '298', '299', '300', '301', '302', '303', '304', '358', '359', '365', '367', '379', '382', '385', '409', '610', '611', '613', '614', '615', '618', '637', '668', '670', '676', '677', '681', '682', '683', '811', '812', '813', '814', '815', '816', '817', '818', '819', '820', '821', '822', '823', '824', '825', '826', '827', '828', '829', '830', '135', '390', '136', '137', '138', '139', '350', '351', '352', '353']


In [ ]:
id2label = {idx: label for idx, label in enumerate(labels)}
print(f"id2label: {type(id2label)} {len(id2label)}\n{id2label}")

id2label: <class 'dict'> 126
{0: '142', 1: '143', 2: '146', 3: '147', 4: '149', 5: '150', 6: '152', 7: '154', 8: '155', 9: '156', 10: '158', 11: '160', 12: '162', 13: '165', 14: '167', 15: '169', 16: '170', 17: '171', 18: '173', 19: '174', 20: '175', 21: '176', 22: '356', 23: '360', 24: '361', 25: '362', 26: '364', 27: '370', 28: '371', 29: '373', 30: '375', 31: '376', 32: '394', 33: '408', 34: '667', 35: '686', 36: '687', 37: '689', 38: '756', 39: '758', 40: '760', 41: '761', 42: '906', 43: '263', 44: '265', 45: '266', 46: '267', 47: '268', 48: '271', 49: '272', 50: '273', 51: '274', 52: '275', 53: '276', 54: '277', 55: '278', 56: '279', 57: '283', 58: '284', 59: '285', 60: '286', 61: '287', 62: '288', 63: '289', 64: '291', 65: '293', 66: '297', 67: '298', 68: '299', 69: '300', 70: '301', 71: '302', 72: '303', 73: '304', 74: '358', 75: '359', 76: '365', 77: '367', 78: '379', 79: '382', 80: '385', 81: '409', 82: '610', 83: '611', 84: '613', 85: '614', 86: '615', 87: '618', 88: '637', 8

In [ ]:
label2id = {label: idx for idx, label in enumerate(labels)}
print(f"label2id: {type(label2id)} {len(label2id)}\n{label2id}")

label2id: <class 'dict'> 126
{'142': 0, '143': 1, '146': 2, '147': 3, '149': 4, '150': 5, '152': 6, '154': 7, '155': 8, '156': 9, '158': 10, '160': 11, '162': 12, '165': 13, '167': 14, '169': 15, '170': 16, '171': 17, '173': 18, '174': 19, '175': 20, '176': 21, '356': 22, '360': 23, '361': 24, '362': 25, '364': 26, '370': 27, '371': 28, '373': 29, '375': 30, '376': 31, '394': 32, '408': 33, '667': 34, '686': 35, '687': 36, '689': 37, '756': 38, '758': 39, '760': 40, '761': 41, '906': 42, '263': 43, '265': 44, '266': 45, '267': 46, '268': 47, '271': 48, '272': 49, '273': 50, '274': 51, '275': 52, '276': 53, '277': 54, '278': 55, '279': 56, '283': 57, '284': 58, '285': 59, '286': 60, '287': 61, '288': 62, '289': 63, '291': 64, '293': 65, '297': 66, '298': 67, '299': 68, '300': 69, '301': 70, '302': 71, '303': 72, '304': 73, '358': 74, '359': 75, '365': 76, '367': 77, '379': 78, '382': 79, '385': 80, '409': 81, '610': 82, '611': 83, '613': 84, '614': 85, '615': 86, '618': 87, '637': 88, '

## Download the tokenizer and the model

In [ ]:
print("Tokenizer")
tokenizer = LongformerTokenizerFast.from_pretrained(repo_id, timeout=60)  # Increased timeout to 60 seconds)

print("Model")
model = LongformerForSequenceClassification.from_pretrained(repo_id)
model.eval()  # Ensures no gradient computation

# Move model to GPU if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model.to(device)

Tokenizer


tokenizer_config.json:   0%|          | 0.00/1.28k [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/798k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/3.56M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/280 [00:00<?, ?B/s]

Model


config.json:   0%|          | 0.00/4.89k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/595M [00:00<?, ?B/s]

LongformerForSequenceClassification(
  (longformer): LongformerModel(
    (embeddings): LongformerEmbeddings(
      (word_embeddings): Embedding(50265, 768, padding_idx=1)
      (token_type_embeddings): Embedding(1, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
      (position_embeddings): Embedding(4098, 768, padding_idx=1)
    )
    (encoder): LongformerEncoder(
      (layer): ModuleList(
        (0-11): 12 x LongformerLayer(
          (attention): LongformerAttention(
            (self): LongformerSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (query_global): Linear(in_features=768, out_features=768, bias=True)
              (key_global): Linear(in_features=768, out_features=768, bias=True)
          

## Downloads the optimized thresholds

In [ ]:
file_path = hf_hub_download(repo_id=repo_id, filename="optimized_thresholds.json", cache_dir="./my_HF_downloads")
print(f"file_path: {file_path}")

# Load the JSON file
with open(file_path, 'r') as json_file:
    optimized_thresholds_json = json.load(json_file)

#print(f"optimized_thresholds_json: {type(optimized_thresholds_json)} {len(optimized_thresholds_json)}")
#print(json.dumps(optimized_thresholds_json, indent=2))

optimized_thresholds = np.array(list(optimized_thresholds_json.values()))
print(f"optimized_thresholds: {type(optimized_thresholds)} shape={optimized_thresholds.shape}\n{optimized_thresholds}")


optimized_thresholds.json:   0%|          | 0.00/3.75k [00:00<?, ?B/s]

file_path: ./my_HF_downloads/models--claudelepere--jobs_EN_791112_50000_041218/snapshots/386e44b282181501fad9ef3382c3a3d7ed69d392/optimized_thresholds.json
optimized_thresholds: <class 'numpy.ndarray'> shape=(126,)
[0.5  0.4  0.45 0.45 0.45 0.45 0.4  0.45 0.45 0.45 0.45 0.5  0.5  0.45
 0.4  0.45 0.5  0.45 0.45 0.45 0.4  0.45 0.5  0.5  0.45 0.4  0.45 0.4
 0.45 0.4  0.45 0.4  0.45 0.45 0.4  0.45 0.35 0.45 0.4  0.35 0.4  0.45
 0.4  0.35 0.4  0.4  0.35 0.4  0.45 0.45 0.45 0.4  0.3  0.45 0.45 0.4
 0.4  0.35 0.45 0.4  0.45 0.4  0.4  0.45 0.45 0.35 0.45 0.45 0.45 0.45
 0.3  0.45 0.45 0.45 0.4  0.45 0.45 0.5  0.4  0.35 0.4  0.45 0.45 0.4
 0.45 0.45 0.45 0.35 0.45 0.35 0.35 0.45 0.45 0.3  0.35 0.4  0.45 0.45
 0.45 0.4  0.35 0.45 0.45 0.5  0.45 0.4  0.5  0.45 0.45 0.45 0.45 0.35
 0.45 0.35 0.45 0.5  0.45 0.45 0.45 0.5  0.45 0.5  0.35 0.35 0.45 0.45]


In [ ]:
def format_int_or_NaN(x):
    return int(x) if not np.isnan(x) else "NaN"

In [ ]:
def calculate_confusion_multi(precision, recall, support, total_samples):
    precision     = np.array(precision)
    recall        = np.array(recall)
    support       = np.array(support)
    total_samples = np.array(total_samples)

    with np.errstate(divide='ignore', invalid='ignore'):
        f1_score = 2 * (precision * recall) / (precision + recall)
        TP       = recall * support
        FN       = support - TP
        FP       = TP * (1 - precision)/precision
        TN       = total_samples - TP - FN - FP

    return pd.DataFrame({
        'TP' : TP,
        'FN' : FN,
        'FP' : FP,
        'TN' : TN
    })

In [ ]:
def analyze_multi_label_performance(y_true, y_pred, label_names=None, plot=True):
    """
    Returns:
    - label_df    : per-label precision, recall, f1, support (DataFrame)
    - summary_df  : micro, macro, weighted and samples averages (DataFrame)
    - confusion_df: per-label TP, FP, FN, TN (DataFrame)
    """
    report_dict = classification_report(
        y_true, y_pred,
        target_names=label_names,
        zero_division="warn",
        output_dict=True
    )
    report_df = pd.DataFrame(report_dict).T
    #print(f"report_df: {type(report_df)} shape={report_df.shape}\n{report_df}")

    # label_df
    label_df = report_df.loc[label_names].copy()
    label_df['support'] = label_df['support'].apply(format_int_or_NaN)
    #print(f"label_df: {type(label_df)} shape={label_df.shape}\n{label_df}")

    precision = label_df['precision'].values
    recall    = label_df['recall'].values
    f1_score  = label_df['f1-score'].values
    support   = label_df['support'].values

    total_samples = len(y_true)
    print(f"total_samples: {type(total_samples)} {total_samples}")  # <class 'int'> 1000
    total_support = label_df['support'].sum()
    print(f"total_support: {type(total_support)} {total_support}")  # <class 'numpy.float64'> 6441.0

    confusion_df       = calculate_confusion_multi(precision, recall, support, total_samples)
    confusion_df.index = label_names
    confusion_df       = confusion_df.applymap(format_int_or_NaN)
    #print(f"confusion_df: {type(confusion_df)} shape={confusion_df.shape}\n{confusion_df}")

    # All average rows: micro, macro, weighted, samples
    avg_rows      = ["micro avg", "macro avg", "weighted avg", "samples avg"]
    existing_avgs = [row for row in avg_rows if row in report_df.index]

    summary_df            = report_df.loc[existing_avgs, ["precision", "recall", "f1-score", "support"]]
    summary_df.loc["micro avg", "support"]    = total_support
    summary_df.loc["macro avg", "support"]    = np.nan         # no clear meaning
    summary_df.loc["weighted avg", "support"] = total_support  # number of samples
    summary_df.loc["samples avg", "support"]  = total_samples  # number of samples
    summary_df["support"]                     = summary_df["support"].apply(format_int_or_NaN)
    #print(f"summary_df: {type(summary_df)} shape={summary_df.shape}\n{summary_df}"


    # Optional plot
    if plot:
        #label_df[["precision", "recall", "f1", "support"]].plot(
        label_df[["precision", "recall", "support"]].plot(
            kind="bar", figsize=(10,6), ylim=(0,1),
            title="Per-Label Precision Recall F1 Support"
        )
        plt.grid(axis='y')
        plt.ylabel("Score")
        plt.tight_layout()
        plt.show()

    return label_df, confusion_df, summary_df



## case TP=0 FN!=0 and case TP=0 FN=0

|label|TP|FN|FP|TN|label|precision|recall|f1|support|
|:---:|::|::|::|::|:---:|:-------:|:----:|::|:-----:|
|266|0|3|NaN|NaN|266|0.00|0.00|0.00|3|
|267|0|2|NaN|NaN|267|0.00|0.00|0.00|2|
|273|0|3|NaN|NaN|273|0.00|0.00|0.00|3|
|275|0|0|NaN|NaN|275|0.00|0.00|0.00|0|
|279|0|1|NaN|NaN|279|0.00|0.00|0.00|1|
|285|0|3|NaN|NaN|285|0.00|0.00|0.00|3|
|301|0|0|NaN|NaN|301|0.00|0.00|0.00|0|
|618|0|0|NaN|NaN|618|0.00|0.00|0.00|0|
|681|0|3|NaN|NaN|681|0.00|0.00|0.00|3|
|815|0|1|NaN|NaN|815|0.00|0.00|0.00|1|
|825|0|1|NaN|NaN|825|0.00|0.00|0.00|1|

- TP=0 and FN!=0:
 - precision = 0
 - recall    = 0
 - f1        = 0
 - support   = FN (some true positives to be found)
- TP=FN=0:
 - precision = 0/0 (undefined)
 - recall    = 0/0 (undefined)
 - f1        = 0/0 (undefined)
 - support   = 0   (label never present in the ground truth, the model never predicted it)
- From jobs_preprocessing - CounterPrediction:
 - count_275: <class 'int'> 0
 - count_301: <class 'int'> 0
 - count_618: <class 'int'> 0

In [ ]:
# Step 1: Tokenize dataset
def tokenize_function(examples):
  return tokenizer(examples["text"], padding='max_length', max_length=max_length, truncation=True)

tokenized_dataset = dataset.map(tokenize_function, batched=True)
# <class 'datasets.arrow_dataset.Dataset'> shape=(100, 10)
#print(f"tokenized_dataset: {type(tokenized_dataset)} shape={tokenized_dataset.shape}\n{tokenized_dataset}")

tokenized_df = tokenized_dataset.to_pandas()
#print(f"tokenized_df: {type(tokenized_df)} shape={tokenized_df.shape}\n{tokenized_df}")

# Step 2: Convert to PyTorch DataLoader
tokenized_dataset.set_format(type="torch", columns=["input_ids", "attention_mask"] + labels)
dataloader = DataLoader(tokenized_dataset, batch_size=batch_size)

# Step 3: Run Prediction
all_preds = []

with torch.no_grad():                       # No gradients needed for prediction
    for batch in dataloader:
        # Move batch to GPU if available
        inputs = {k: batch[k].to(device) for k in ["input_ids", "attention_mask"]}

        # Forward pass
        outputs = model(**inputs)
        logits = outputs.logits  # Model outputs raw logits

        # Apply sigmoid to convert logits into probabilities
        probs = torch.sigmoid(logits)

        # Move probs to CPU and convert to NumPy
        all_preds.extend(probs.cpu().numpy())

all_preds_arr = np.array(all_preds)
#print(f"all_preds    : {type(all_preds)}     len={len(all_preds)}\n{all_preds}")
#print(f"all_preds_arr: {type(all_preds_arr)} shape={all_preds_arr.shape}\n{all_preds_arr}")

# Step 4: Convert Probabilities to Binary Predictions
if threshold_tuning:
    thresholds = optimized_thresholds
else:
    thresholds = np.full(num_labels, 0.5)
print(f"thresholds: {type(thresholds)} shape={thresholds.shape}\n{thresholds}")                  # <class 'numpy.ndarray'> shape=(6,)
print()

binary_preds = (np.array(all_preds) > thresholds).astype(int)
#print(f"binary_preds: {type(binary_preds)} shape={binary_preds.shape}\n{binary_preds}")          # <class 'numpy.ndarray'> shape=(100, 6)

# Step 5: Compare with True Labels
true_labels = tokenized_df[labels]
#print(f"true_labels: {type(true_labels)} shape={true_labels.shape}\n{true_labels}")              # <class 'pandas.core.frame.DataFrame'> shape=(100, 6)

# Convert true_labels DataFrame to a NumPy array of 0 and 1
true_labels_np  = true_labels.astype(int).to_numpy()
#print(f"true_labels_np: {type(true_labels_np)} shape={true_labels_np.shape}\n{true_labels_np}")  # <class 'numpy.ndarray'> shape=(100, 6)

# Convert id2label dict to a list of label names
label_names = list(id2label.values())
print(f"label_names: {type(label_names)} len={len(label_names)}\n{label_names}")  # <class 'list'> len=126
print()

#classification_report(y_true, y_pred)
report = classification_report(
    true_labels_np, binary_preds, target_names=label_names, zero_division="warn")
print(f"classification report:{type(report)} len={len(report)}\n{report}")      # <class 'str'> len=7076
print()

#report2 = classification_report(true_labels_np, binary_preds, target_names=label_names, zero_division="warn", output_dict=True)
#print(f"classification report2:{type(report2)} len={len(report2)}\n{report2}")  # <class 'dict'> len=130
#print()

label_df, confusion_df, summary_df = analyze_multi_label_performance(
    true_labels_np, binary_preds, label_names=label_names, plot=False)

label_df[['precision', 'recall', 'f1-score']] = label_df[['precision', 'recall', 'f1-score']].round(2)
label_df['support'] = label_df['support'].astype(int)

summary_df[['precision', 'recall', 'f1-score']] = summary_df[['precision', 'recall', 'f1-score']].round(2)

print("__________________________________________")

print("\nclassification report (= label_df):\n", label_df)

print("__________________________________________")

print("\nAll averages:\n", summary_df)

print("__________________________________________")

#pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
#pd.set_option('display.max_colwidth', None)
print("\nConfusion matrix:")
print("precision = TP / (TP+FP)")
print("recall    = TP / (TP+FN)")
print("1/f1      = 1/2 * 1/precision + 1/recall")
print("support   = TP+FN")
print("\nConfusion matrix:\n", confusion_df)

print("__________________________________________")

#raise Exception("I stop here")
df_compare                = df_original.copy()
df_compare['true_labels'] = true_labels.values.tolist()
df_compare['preds']       = binary_preds.tolist()
df_compare['compare']     = (df_compare['true_labels']==df_compare['preds']).replace({True:'OK', False:'KO'})
#print(f"df_compare: {type(df_compare)} shape={df_compare.shape}\n{df_compare}")  # <class 'pandas.core.frame.DataFrame'>
print()

def print_row(row, file):
    """Prints the row information to the console and writes it to a file."""
    output  = f"id: {row['id']}\n"
    output += f"text: {row['text']}\n"
    output += "labels     : [" + ", ".join(f"{label:>5}" for label in labels) + "]\n"
    output += "true_labels: [" + ", ".join(f"{true_label:>5}" for true_label in row['true_labels']) + "]\n"
    output += "preds      : [" + ", ".join(f"{pred:>5}" for pred in row['preds']) + "]\n"
    output += f"compare    : {row['compare']}\n"
    output += "\n"

    print(output, end="")  # Print to console without extra newline
    file.write(output)     # Write to file

# Open the file in write mode
with open("output.txt", "w") as f:
    _ = df_compare.apply(print_row, axis=1, args=(f,))  # Pass file object to print_row

files.download("/content/output.txt")

# Count total 'OK' and 'KO' values
total_ok = (df_compare['compare'] == 'OK').sum()  # Total matches
total_ko = (df_compare['compare'] == 'KO').sum()  # Total mismatches
print(f"Total 'OK': {total_ok}")
print(f"Total 'KO': {total_ko}")
print()

Map:   0%|          | 0/1000 [00:00<?, ? examples/s]

Initializing global attention on CLS token...


thresholds: <class 'numpy.ndarray'> shape=(126,)
[0.5  0.4  0.45 0.45 0.45 0.45 0.4  0.45 0.45 0.45 0.45 0.5  0.5  0.45
 0.4  0.45 0.5  0.45 0.45 0.45 0.4  0.45 0.5  0.5  0.45 0.4  0.45 0.4
 0.45 0.4  0.45 0.4  0.45 0.45 0.4  0.45 0.35 0.45 0.4  0.35 0.4  0.45
 0.4  0.35 0.4  0.4  0.35 0.4  0.45 0.45 0.45 0.4  0.3  0.45 0.45 0.4
 0.4  0.35 0.45 0.4  0.45 0.4  0.4  0.45 0.45 0.35 0.45 0.45 0.45 0.45
 0.3  0.45 0.45 0.45 0.4  0.45 0.45 0.5  0.4  0.35 0.4  0.45 0.45 0.4
 0.45 0.45 0.45 0.35 0.45 0.35 0.35 0.45 0.45 0.3  0.35 0.4  0.45 0.45
 0.45 0.4  0.35 0.45 0.45 0.5  0.45 0.4  0.5  0.45 0.45 0.45 0.45 0.35
 0.45 0.35 0.45 0.5  0.45 0.45 0.45 0.5  0.45 0.5  0.35 0.35 0.45 0.45]

label_names: <class 'list'> len=126
['142', '143', '146', '147', '149', '150', '152', '154', '155', '156', '158', '160', '162', '165', '167', '169', '170', '171', '173', '174', '175', '176', '356', '360', '361', '362', '364', '370', '371', '373', '375', '376', '394', '408', '667', '686', '687', '689', '756', '75

/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Total 'OK': 40
Total 'KO': 960



In [ ]:
print("It's the end")

It's the end


In [ ]:
raise Exception("I stop here")

Exception: I stop here